## AIMI High School Internship 2023
### Notebook 2: Training a Vision Model to Predict ET Distances

**The Problem**: Given a chest X-ray, our goal in this project is to predict the distance from an endotracheal tube to the carina. This is an important clinical task - endotracheal tubes that are positioned too far (>5cm) above the carina will not work effectively.

**Your Second Task**: You should now have a training dataset consisting of (a) chest X-rays and (b) annotations indicating the distance of the endotracheal tube from the carina. Now, your goal is to train a computer vision model to predict endotracheal tube distance from the image. You have **two options** for this task, and you may attempt one or both of these:
- *Distance Categorization* : Train a model to determine whether the position of a tube is abnormal (>5.0 cm) or normal (≤ 5.0 cm).
- *Distance Prediction*: Train a model that predicts the distance of the endotracheal tube from the carina in centimeters.

In this notebook, we provide some simple starter code to get you started on training a computer vision model. You are not required to use this template - feel free to modify as you see fit.

**Submitting Your Model**: We have created a leaderboard where you can submit your model and view results on the held-out test set. We provide instructions below for submitting your model to the leaderboard. **Please follow these directions carefully**.

We will evaluate your results on the held-out test set with the following evaluation metrics:
- *Distance Categorization* : We will measure AUROC, which is a metric commonly used in healthcare tasks. See this blog for a good explanation of AUROC: https://glassboxmedicine.com/2019/02/23/measuring-performance-auc-auroc/
- *Distance Prediction*: We will measure the mean average error (also known as L1 distance) between the predicted distances and the true distances.


## Load Data
Before you begin, make sure to go to `Runtime` > `Change Runtime Type` and select a T4 GPU. Then, upload `data.zip`. It should take about 10 minutes for these files to be uploaded. Then, run the following cells to unzip the dataset (which should take < 10 seconds)

## Import Libraries
We are leveraging the PyTorch framework to train our models. For more information and tutorials on PyTorch, see this link: https://pytorch.org/tutorials/beginner/basics/intro.html

In [3]:
# Some libraries that you may find useful are included here.
# To import a library that isn't provided with Colab, use the following command: !pip install torchmetrics
import torch
import pandas as pd
from PIL import Image
import numpy as np
from tqdm import tqdm
from torchvision import transforms


## Create Dataloaders
We will implement a custom Dataset class to load in data. A custom Dataset class must have three methods: `__init__`, which sets up any class variables, `__len__`, which defines the total number of images, and `__getitem__`, which returns a single image and its paired label.

In [4]:
from torch.utils.data import Dataset
from PIL import Image


class ChestXRayDataset(Dataset):
    def __init__(self, img_paths, labels, distances):
        super(ChestXRayDataset, self).__init__()
        self.img_paths = img_paths
        self.labels = labels
        self.distances = distances
        # Fill in __init__() here

    def __len__(self):

        # Fill in __len__() here
        return self.labels.shape[0]

    def __getitem__(self, idx):
        out_dict = {"idx": torch.tensor(idx),}

        # Fill in __getitem__() here
        img = Image.open(f"data/{self.img_paths[idx]}")
        convert_tensor = transforms.ToTensor()
        img_as_tensor = convert_tensor(img)
        img_as_tensor.requires_grad_ = True
        out_dict["img"] = img_as_tensor
        out_dict["distance"] = self.distances[idx]

        return out_dict

## Define Training Components
Here, define any necessary components that you need to train your model, such as the model architecture, the loss function, and the optimizer.

In [7]:
# loss = # Loss Function
# model = # Model Architecture (make sure to load the model on GPU, not CPU!)
# opt = torch.optim.AdamW(model.parameters(), lr=1e-4) # AdamW is a commonly-used optimizer. Feel free to modify.

data = pd.read_csv("mimic_train_labels_pruned.csv")
img_paths = data["image_path"].to_numpy()
labels = data["positioning"].to_numpy()
distances = data["measures"].to_numpy()

dataset = ChestXRayDataset(img_paths=img_paths, labels=labels, distances=distances)

dataloader = torch.utils.data.DataLoader(dataset=dataset, batch_size=10, shuffle=True, drop_last=True)


11565
{'idx': tensor([ 8084, 11483,  4253, 10698, 10967,  5797,  9482, 10910,   969,  7698]), 'img': tensor([[[[0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          ...,
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
          [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000]]],


        [[[0.0392, 0.0431, 0.0431,  ..., 0.4824, 0.0000, 0.0078],
          [0.0392, 0.0431, 0.0431,  ..., 0.4980, 0.0000, 0.0078],
          [0.0392, 0.0431, 0.0431,  ..., 0.5020, 0.0039, 0.0000],
          ...,
          [0.0588, 0.0588, 0.0588,  ..., 0.0902, 0.0000, 0.0078],
          [0.0588, 0.0588, 0.0627,  ..., 0.0980, 0.0039, 0.0157],
          [0.0314, 0.0314, 0.0314,  ..., 0.0745, 0.0000, 0.0000]]],


        [[[0.0118, 0.0118, 0.0118,  ..., 0.0275, 0.0196, 0.0118],
   

## Training Code
We provide starter code below that implements a simple training loop in PyTorch. Feel free to modify as you see fit.

In [ ]:
def train(model, loss_fn, train_loader, opt, max_epoch):

    best_val_loss = np.inf
    best_val_metrics = []
    for epoch in range(0, max_epoch):
        model.train()

        for step, sample in tqdm(enumerate(train_loader)):
            opt.zero_grad()
            pred = # Compute prediction

            loss = # Compute Loss

            loss.backward()
            opt.step()

In [ ]:
train(model, loss, train_loader, opt, max_epoch=5)

## Submitting Your Results
Once you have successfully trained your model, generate predictions on the test set and save your results as a `.csv` file. This file can then be uploaded to the leaderboard.

Your final `.csv` file **must** have the following format:
- There must be a column titled `image_path` with the paths to the test set images. This column should be identical to the one provided in `mimic_test_student.csv`.
- There must be a column titled `pred` with your model outputs.
  - If you are running the `distance categorization` task, this column must have floating point numbers ranging between 0 and 1. Higher numbers should indicate a greater likelihood that the tube distance is abnormal. Hint: You can convert model outputs to the 0 to 1 range by applying the sigmoid activation function (torch.nn.sigmoid())
  - If you are running the `distance prediction` task, this column must have numbers representing the tube distance in centimeters.
- Double check that there are 500 rows in your output file

In [ ]:
model = # Model Architecture
ckpt = torch.load("/content/best.pkl")
model.load_state_dict(ckpt["state_dict"])

test_dataset = ChestXRayDataset("""Fill in args here""")
test_loader = torch.utils.data.DataLoader(dataset=test_dataset, batch_size=4, shuffle=False, drop_last=False)

test_results = {"image_path": [], "pred": []}
# Write method to load in data from test_loader, compute model predictions, and append results to test_results dict


In [ ]:
test_results = pd.DataFrame(test_results)
test_results.to_csv(f"/content/test.csv")